# Axon Analysis Pipeline

This notebook provides a streamlined workflow for analyzing axon images. It consists of three main parts:

1. **Setup**: Import libraries and set paths
2. **Analysis**: Run the main analysis pipeline
3. **Optional**: Create new regression model

Before running this notebook, make sure you have:
1. Installed dependencies: `conda env create -f utils/environment/environment.yml`
2. Activated the environment: `conda activate axon_analysis`
3. Installed the package: `pip install -e utils/environment`

Note about active configuration:
- New regression models are saved in `REGRESSION_DIR` with timestamps
- To use a model, manually copy it to `Active_Model_and_Configuration_Directory` as `active_model.json`
- The active configuration (`config.yaml`) and regression model are both kept in `Active_Model_and_Configuration_Directory`
- The analysis always uses the configuration and model from this directory


In [1]:
# ===== 1. SETUP =====

# Import required libraries
import os
import sys
import yaml
import numpy as np
from pathlib import Path
from datetime import datetime
import importlib.util
import matplotlib.pyplot as plt
import subprocess
import glob
import shutil

# Enable interactive matplotlib mode
%matplotlib notebook
plt.ion()

# Install and import widget packages
def install_package(package):
    subprocess.check_call([sys.executable, "-m", "pip", "install", package])

required_packages = ['ipywidgets']
for package in required_packages:
    try:
        importlib.import_module(package)
    except ImportError:
        print(f"Installing {package}...")
        install_package(package)
        print(f"{package} installed successfully!")

import ipywidgets as widgets
from IPython.display import display, clear_output

# Add the project root and utils/Confocal to Python path
project_root = os.path.abspath('.')
confocal_dir = os.path.join(project_root, 'utils', 'Confocal')

for path in [project_root, confocal_dir]:
    if path not in sys.path:
        sys.path.insert(0, path)

# Import local modules
from config_manager import load_config, ConfigManager, AnalysisConfig

# Import the main analysis function using importlib for hyphenated filename
spec = importlib.util.spec_from_file_location("branch_based_snakes", "utils/Confocal/branch-based-snakes.py")
branch_based_snakes = importlib.util.module_from_spec(spec)
spec.loader.exec_module(branch_based_snakes)
run_analysis = branch_based_snakes.run_analysis

# Set paths
print("\nPath Configuration:")
print("=" * 80)

# Input Directory: Contains your raw data organized in Group_X/Condition_Y folders
# Example structure:
#   Confocal_Dataset/
#     Group_A/
#       Condition_A/  (KO)
#       Condition_B/  (WT)
#       Condition_C/  (E2)
#       Condition_D/  (E4)
#     Group_B/
#       ...etc
INPUT_DIR = "/Users/charlessander/Desktop/patzke lab computing/Sudhof Lab/Axon Analysis Pipeline/Confocal_Dataset"
print("1. INPUT_DIR:")
print("   - Where your raw ND2 files are stored")
print("   - Must be organized in Group_X/Condition_Y folders")

# Output Directory: Where all results will be saved
# Structure created:
#   Data_Output/
#     Images/processed/  - Summary plots for each image
#     Debug/            - Component visualizations
#     Plots/           - Overall analysis plots
#     Data/            - CSV files and raw data
#     Summaries/       - Summary reports
OUTPUT_DIR = "/Users/charlessander/Desktop/patzke lab computing/Sudhof Lab/Axon Analysis Pipeline/Data_Output"
print("\n2. OUTPUT_DIR:")
print("   - Where all analysis results are saved")
print("   - Creates organized subdirectories for different outputs")
print("   - Main CSVs will be in the root of this directory")

# Regression Models Directory: Stores all created regression models
# Each model consists of:
#   - .json file: The model parameters
#   - .txt file:  Documentation and metadata
#   - .png file:  Regression plot visualization
REGRESSION_DIR = "/Users/charlessander/Desktop/patzke lab computing/Sudhof Lab/Axon Analysis Pipeline/thresholding_regression_models/Confocal Models"
print("\n3. REGRESSION_DIR:")
print("   - Where new regression models are saved")
print("   - Each model has .json, .txt, and .png files")
print("   - Models are timestamped for version control")

# Active Configuration Directory: Contains both configuration and active model
# Files that MUST be here:
#   - config.yaml: Active configuration file (REQUIRED)
#   - active_model.json: The model being used for analysis
#   - active_model.txt:  Documentation for active model
#   - active_model_regression_plot.png: Visualization
ACTIVE_CONFIG_DIR = "/Users/charlessander/Desktop/patzke lab computing/Sudhof Lab/Axon Analysis Pipeline/Active_Model_and_Configuration_Directory"
print("\n4. ACTIVE_CONFIG_DIR:")
print("   - Contains both the active configuration and regression model")
print("   - config.yaml MUST be in this directory")
print("   - Copy model files here as active_model.json to use a different model")
print("   - The analysis always uses config.yaml and active_model.json from this directory")

print("\n" + "=" * 80)

print("Setup complete! All libraries imported and paths set.")



Path Configuration:
1. INPUT_DIR:
   - Where your raw ND2 files are stored
   - Must be organized in Group_X/Condition_Y folders

2. OUTPUT_DIR:
   - Where all analysis results are saved
   - Creates organized subdirectories for different outputs
   - Main CSVs will be in the root of this directory

3. REGRESSION_DIR:
   - Where new regression models are saved
   - Each model has .json, .txt, and .png files
   - Models are timestamped for version control

4. ACTIVE_CONFIG_DIR:
   - Contains both the active configuration and regression model
   - config.yaml MUST be in this directory
   - Copy model files here as active_model.json to use a different model
   - The analysis always uses config.yaml and active_model.json from this directory

Setup complete! All libraries imported and paths set.


In [2]:
# ===== 2. RUN ANALYSIS =====

# Import analysis utilities
from utils.Confocal.analysis_utils import load_and_configure_analysis, run_analysis

# Load configuration and run analysis
config = load_and_configure_analysis(INPUT_DIR, OUTPUT_DIR, ACTIVE_CONFIG_DIR)
run_analysis(config)


Found 4 groups: ['Group_A', 'Group_B', 'Group_C', 'Group_D']
Found 4 conditions: ['Condition_A', 'Condition_B', 'Condition_C', 'Condition_D']

Loaded configuration from: /Users/charlessander/Desktop/patzke lab computing/Sudhof Lab/Axon Analysis Pipeline/Active_Model_and_Configuration_Directory/config.yaml

Starting analysis...

=== L1CAM Analysis - Sliding Window Processing ===
Input directory: /Users/charlessander/Desktop/patzke lab computing/Sudhof Lab/Axon Analysis Pipeline/Confocal_Dataset
Output directory: /Users/charlessander/Desktop/patzke lab computing/Sudhof Lab/Axon Analysis Pipeline/Data_Output
Min sizes to analyze: [30]
Conditions: ['Condition_A', 'Condition_B', 'Condition_C', 'Condition_D']

=== Threshold Parameters ===
Using manual regression parameters:
• Intercept: 82.5909
• Coefficient: 0.3027
• Percentile: 15
• Replicate offsets: {'Group_A': -35, 'Group_B': 5, 'Group_C': 20, 'Group_D': -35}


Using hierarchical structure: Groups -> Conditions -> ND2 files
Groups: ['Gr

<IPython.core.display.Javascript object>

      Calculating thickness statistics...
      Avg thickness (remaining skeleton): 3.74 px
      Avg blue-region thickness:   2.96 px  (n=3416)
      Avg pink-region thickness:   4.22 px  (n=5639)
      Creating component visualization...
        Found 107 blue components (after removing pink regions)
        Found 107 blue components (after removing pink regions)

--- Processing file 2/198: B114 Map2 L1CAM TuJ1  ApoE KO003.nd2 ---
  Group (Biological Replicate): Group_A
  Condition: Condition_A
  Loading image data...
  Found FITC channel at index 0
  Extracting green channel and creating max projection...
  Max projection shape: (1024, 1024)
  Calculating adaptive threshold...
  Group Group_A, threshold offset: -35
  Calculated threshold: 63.52
  Thresholded pixels: 143600
  Checking for TRITC channel (soma removal)...
  Found TRITC channel at index 1
  Processing TRITC channel for soma removal...
  Initial TRITC mask pixels: 62644
  Final soma mask pixels: 23572
    Processing min_

<IPython.core.display.Javascript object>

      Calculating thickness statistics...
      Avg thickness (remaining skeleton): 3.48 px
      Avg blue-region thickness:   2.90 px  (n=3140)
      Avg pink-region thickness:   3.74 px  (n=6958)
        Found 107 blue components (after removing pink regions)

--- Processing file 3/198: B114 Map2 L1CAM TuJ1  ApoE KO001.nd2 ---
  Group (Biological Replicate): Group_A
  Condition: Condition_A
  Loading image data...
  Found FITC channel at index 0
  Extracting green channel and creating max projection...
  Max projection shape: (1024, 1024)
  Calculating adaptive threshold...
  Group Group_A, threshold offset: -35
  Calculated threshold: 68.34
  Thresholded pixels: 239740
  Checking for TRITC channel (soma removal)...
  Found TRITC channel at index 1
  Processing TRITC channel for soma removal...
  Initial TRITC mask pixels: 97229
  Final soma mask pixels: 28192
    Processing min_size=30...
      Removing small objects...
      Pixels after small object removal: 220241
      Applying 

...

    Processing BLUE condition Condition_A with 49 images...
    Processing BLUE condition Condition_B with 48 images...
    Processing BLUE condition Condition_C with 49 images...
    Processing BLUE condition Condition_D with 50 images...

=== Creating PINK-ONLY Summary Plots ===
  Creating PINK-ONLY overlay CDF for min_size=30...


<IPython.core.display.Javascript object>

    Processing PINK condition Condition_A with 49 images...
    Processing PINK condition Condition_B with 48 images...
    Processing PINK condition Condition_C with 48 images...
    Processing PINK condition Condition_D with 50 images...

=== Creating Normalized Component CDFs ===
  Creating normalized component data for min_size=30...
    Saved normalized component data: /Users/charlessander/Desktop/patzke lab computing/Sudhof Lab/Axon Analysis Pipeline/Data_Output/normalized_component_data_min30.csv
    Creating normalized CDF plot...


<IPython.core.display.Javascript object>

    Saved normalized CDF plot: /Users/charlessander/Desktop/patzke lab computing/Sudhof Lab/Axon Analysis Pipeline/Data_Output/Plots/normalized_component_cdf.png

=== Generating CSV Reports ===
  Creating CSV reports for min_size=30...
    Saved per-image data: /Users/charlessander/Desktop/patzke lab computing/Sudhof Lab/Axon Analysis Pipeline/Data_Output/Results/avg_thickness_per_image_min30.csv
    Saved per-condition data: /Users/charlessander/Desktop/patzke lab computing/Sudhof Lab/Axon Analysis Pipeline/Data_Output/Results/avg_thickness_per_condition_min30.csv

=== Generating Component-Level CSV Reports ===
  Creating component-level CSV for min_size=30...
    Saved thick vs thin data: /Users/charlessander/Desktop/patzke lab computing/Sudhof Lab/Axon Analysis Pipeline/Data_Output/thick_thin_data_min30.csv
    Saved normalized thick vs thin data: /Users/charlessander/Desktop/patzke lab computing/Sudhof Lab/Axon Analysis Pipeline/Data_Output/normalized_thick_thin_data_min30.csv
    

In [2]:
# ===== 3. CREATE NEW REGRESSION MODEL (OPTIONAL) =====

# Import regression utilities
import importlib.util
from utils.Confocal.analysis_utils import handle_new_regression_model

# Import regression model module
spec = importlib.util.spec_from_file_location(
    "confocal_threshold_regression",
    os.path.join(REGRESSION_DIR, "confocal_threshold_regression.py")
)
regression_module = importlib.util.module_from_spec(spec)
spec.loader.exec_module(regression_module)

# Parameters for interactive model creation
NUM_FILES = 10          # Number of random files to sample from input directory
MIN_THRESHOLD = 0       # Minimum value for threshold slider
MAX_THRESHOLD = 500     # Maximum value for threshold slider
STEP_SIZE = 1.0        # Step size for threshold slider
METRIC_PERCENTILE = 15  # Percentile for calculating mean above metric

print(f"Starting interactive regression model creation...")
print(f"Will sample {NUM_FILES} random files from: {INPUT_DIR}")
print(f"Threshold range: {MIN_THRESHOLD} to {MAX_THRESHOLD} (step: {STEP_SIZE})")
print(f"Using {METRIC_PERCENTILE}th percentile for mean above metric calculation")
print("Use the slider to adjust threshold and click 'Finish Now' when satisfied.")

# Create new regression model
try:
    regression_module.create_interactive_model(
        input_dir=INPUT_DIR,
        num_files=NUM_FILES,
        min_threshold=MIN_THRESHOLD,
        max_threshold=MAX_THRESHOLD,
        threshold_step=STEP_SIZE,
        metric_percentile=METRIC_PERCENTILE
    )
    handle_new_regression_model(REGRESSION_DIR, ACTIVE_CONFIG_DIR)
except Exception as e:
    print(f"\nError occurred: {str(e)}")
    raise


Output()


Image info:
  File: B114 Map2 L1CAM TuJ1  ApoE2009.nd2
  Replicate: B114
  Mean above 15th percentile: 124.45
  Current threshold: 250.0
  Slider range: 0-500

Move the slider to adjust the threshold - binary mask will update automatically

No regression model was created. Please try again.
